In [1]:
import math
from scipy.optimize import minimize
import numpy as np

In [2]:
### tools：

def minfunction(f, x0, bounds):
    """
    求一个函数在边界内的最小值
    f：函数
    x0：初始值
    bounds：边界条件。[(min, max),...]
    """
    res = minimize(f, x0, method='SLSQP', bounds=bounds)
    return res

def maxfunction(f, x0, bounds):
    """
    求一个函数在边界内的最大值
    f：函数
    x0：初始值
    bounds：边界条件。[(min, max),...]
    """
    fun = lambda X : -f(X)
    res = minimize(fun, x0, method='SLSQP', bounds=bounds)
    return res


In [3]:
bounds = [(-10, 10), (-10, 10), (-10, 10), (-10, 10), (-10, 10), (-10, 10), (-10, 10), (-10, 10), (-10, 10), (-10, 10)]
x_opt = [2.17199634142692, 2.3636830416034, 8.77392573913157, 5.09598443745173, 0.990654756560493, 1.43057392853463,
         1.32164415364306, 9.82872576524495, 8.2800915887356, 8.3759266477347]
y_opt = 24.30620906818
def G07(X):
    y = X[0] * X[0] + X[1] * X[1] + X[0] * X[1] - 14 * X[0] - 16 * X[1] + (X[2] - 10) ** 2 + 4 * (X[3] - 5) ** 2 + (
            X[4] - 3) ** 2 + 2 * (X[5] - 1) ** 2 + 5 * X[6] * X[6] + 7 * (X[7] - 11) ** 2 + 2 * (X[8] - 10) ** 2 + (
                X[9] - 7) ** 2 + 45

    g1 = -105 + 4 * X[0] + 5 * X[1] - 3 * X[6] + 9 * X[7]
    g2 = 10 * X[0] - 8 * X[1] - 17 * X[6] + 2 * X[7]
    g3 = -8 * X[0] + 2 * X[1] + 5 * X[8] - 2 * X[9] - 12
    g4 = 3 * (X[0] - 2) ** 2 + 4 * (X[1] - 3) ** 2 + 2 * X[2] * X[2] - 7 * X[3] - 120
    g5 = 5 * X[0] * X[0] + 8 * X[1] + (X[2] - 6) ** 2 - 2 * X[3] - 40
    g6 = X[0] * X[0] + 2 * (X[1] - 2) ** 2 - 2 * X[0] * X[1] + 14 * X[4] - 6 * X[5]
    g7 = 0.5 * (X[0] - 8) ** 2 + 2 * (X[1] - 4) ** 2 + 3 * X[4] * X[4] - X[5] - 30
    g8 = -3 * X[0] + 6 * X[1] + 12 * (X[8] - 8) ** 2 + - 7 * X[9]

    return y, g1, g2, g3, g4, g5, g6, g7, g8

In [4]:
# y = lambda X: G07(X)[0]
# g1 = lambda X: G07(X)[1]
# g2 = lambda X: G07(X)[2]
# g3 = lambda X: G07(X)[3]
# g4 = lambda X: G07(X)[4]
# g5 = lambda X: G07(X)[5]
# g6 = lambda X: G07(X)[6]
# g7 = lambda X: G07(X)[7]
# g8 = lambda X: G07(X)[8]
# # x0 = [1,2,3,4,5,6,7,8,9,10]
# # x0 = [-10,-10,-10,-10,-10,-10,-10,-10,-10,-10]
# # x0 = [0,0,0,0,0,0,0,0,0,0]
# # x0 = [10,10,10,10,10,10,10,10,10,10]

In [5]:
# minfunction(y,x0,bounds)

In [6]:
### 适应度函数
def fitnessG07_num(X, epsion):
    """
    problem1关于数量惩罚的适应度函数
    X: 对应的解
    epsion：惩罚系数大于fmax-fmin的倍数
    """
    fmax = 1220.174
    fmin = 0.008509619375000003
    count = np.sum(np.array(problem1(X))[1:5]>0)
    
    return -(problem1(X)[0]+epsion*(fmax-fmin)*count)  

def fitnessG07_vio(X):
    """
    problem1关于数量惩罚的适应度函数
    X: 对应的解
    epsion：惩罚系数大于fmax-fmin的倍数
    """
    fmax = 7032
    fmin = -24
    vmax = 4329
    e = 0.1
    n = 8
    
    res = G07(X)
    fitness = -res[0]
    count = np.sum(np.array(res)[1:9]>0)
    
    if count > 0:
        for i in range(1,len(res)):
            if res[i] > 0:
                cathy = (fmax - fmin)*(e*vmax*n/count+res[i])/(e*vmax)
                fitness = fitness - cathy
    return fitness 


In [7]:
### PSO
class PSO_fit():
    def __init__(self, pN, dim, max_iter, bounds):
        self.wmax = 0.8 #最大的惯性权重
        self.wmin = 0.4 #最小的惯性权重
        self.c1 = 2  #加速因子
        self.c2 = 2  #加速因子
        self.pN = pN  # 粒子数量
        self.dim = dim  # 搜索维度
        self.max_iter = max_iter  # 迭代次数
        self.bounds = bounds
        
        self.X = np.zeros((self.pN, self.dim))  # 所有粒子的位置：一个pN*dim的矩阵
        self.V = np.zeros((self.pN, self.dim))  # 左右粒子的速度：一个pN*dim的矩阵
        self.pbest = np.zeros((self.pN, self.dim))  # 个体经历的最佳位置：一个pN*dim的矩阵
        self.gbest = np.zeros((self.pN, self.dim))      # 全局最佳位置：一个pN*dim的矩阵
        self.p_fit = np.full(self.pN,-100000000.0)  # 每个个体的历史最佳适应值
        self.g_fit = np.full(self.pN,-100000000.0)    # 全局最佳适应值
    
    def init_Population(self):
        """
        初始化种群
        :return:
        """
        
        for i in range(self.pN):
            for j in range(self.dim):
                self.X[i][j] = self.bounds[j][0] + (self.bounds[j][1] - self.bounds[j][0]) * np.random.random()
                self.V[i][j] = self.bounds[j][0] + (self.bounds[j][1] - self.bounds[j][0]) * np.random.random()
        for i in range(self.pN):
            tmp = fitnessG07_vio(self.X[i])
            if (tmp > self.p_fit[i]):
                self.p_fit[i] = tmp
                self.pbest[i] = self.X[i]
                
        for i in range(self.pN):
            indexes = np.random.randint(low=0,high=self.pN,size=int(self.pN/100))
            for j in indexes:
                if self.p_fit[j] > self.g_fit[i]:
                    self.g_fit[i] = self.p_fit[j]
                    self.gbest[i] = self.pbest[j]

#             self.pbest[i] = self.X[i]
#             tmp = fitnessG01_num(self.X[i])
#             self.p_fit[i] = tmp
#             if (tmp > self.fit):
#                 self.fit = tmp
#                 self.gbest = self.X[i]
        
    def iterator(self):
        """
        迭代
        """
        for t in range(self.max_iter):
            w = self.wmin + (self.wmax - self.wmin) * np.exp(- (4 * t / self.max_iter) * (4 * t / self.max_iter))
            
            for i in range(self.pN):
                self.V[i] = w*self.V[i]+self.c1*np.random.random()*(self.pbest[i]-self.X[i])+self.c2*np.random.random()*(self.gbest[i]-self.X[i])
                self.X[i] = self.X[i] + self.V[i]
                
                """
                控制在搜索范围内
                """ 
                for j in range(self.dim):
                    if self.X[i][j] < self.bounds[j][0]:
                        self.X[i][j] = self.bounds[j][0]
                    if self.X[i][j] > self.bounds[j][1]:
                        self.X[i][j] = self.bounds[j][1]     
            for i in range(self.pN):
                tmp = fitnessG07_vio(self.X[i])
                if (tmp > self.p_fit[i]):
                    self.p_fit[i] = tmp
                    self.pbest[i] = self.X[i]
            for i in range(self.pN):
                indexes = np.random.randint(low=0,high=self.pN,size=int(self.pN/100))
                for j in indexes:
                    if self.p_fit[j] > self.g_fit[i]:
                        self.g_fit[i] = self.p_fit[j]
                        self.gbest[i] = self.pbest[j]
            print(self.g_fit)  
        return self.gbest, self.g_fit

In [8]:
PSO = PSO_fit(pN=1000, dim=10, max_iter=500, bounds=bounds)

In [9]:
PSO.init_Population()

In [10]:
gbest,g_fit = PSO.iterator()

[-63151.79267079 -60422.57422092 -60137.71975076 -61879.68858435
 -65238.99352024 -62117.70696741 -62339.6068422  -63557.43762957
 -59801.59345676 -61952.29197159 -61244.70436502 -61879.68858435
 -66338.48484363 -58707.12476477 -57790.54610343 -57490.97947831
 -61992.41797643 -64508.27568814 -58707.12476477 -63271.04945653
 -57490.97947831 -61426.16227016 -61839.39838599 -65178.11421514
 -65454.58077266 -60392.66623168 -59801.59345676 -60861.42725094
 -62489.54106469 -65178.11421514 -60137.71975076 -67058.74861703
 -57790.54610343 -57490.97947831 -66772.04267523 -60839.37566163
 -58429.6384859  -63343.74137305 -59801.59345676 -59697.7874317
 -60842.48946393 -63847.51200152 -60052.80954325 -60686.44508697
 -62903.59486615 -64222.25671182 -62712.67294816 -60842.48946393
 -63663.41314134 -59801.59345676 -65695.2720466  -62505.358042
 -64084.43186954 -60052.80954325 -63557.43762957 -62028.43774723
 -63459.88553811 -63537.21364253 -60693.16368906 -63343.74137305
 -60466.1341017  -61300.7734

[-57490.97947831 -59394.67299862 -59068.40640521 -58935.64668703
 -58328.46551327 -60005.3662766  -59610.66386492 -58454.96922895
 -58507.04229014 -58486.7569697  -58449.29855329 -58667.02514082
 -57790.54610343 -58707.12476477 -57245.91099312 -57490.97947831
 -58283.15158291 -57490.97947831 -57396.16079285 -58328.46551327
 -57490.97947831 -57558.2156764  -58013.64655837 -57790.54610343
 -58283.15158291 -59243.17484815 -59277.61289486 -58414.06180521
 -58152.36249948 -59871.213318   -59181.72847303 -57490.97947831
 -57790.54610343 -57470.14831287 -59181.72847303 -58429.6384859
 -58429.6384859  -58414.06180521 -59801.59345676 -57558.2156764
 -59171.9543728  -57490.97947831 -59465.38033707 -59123.67532746
 -58667.02514082 -59033.14719992 -59048.61299109 -58225.79985962
 -58667.02514082 -59801.59345676 -59023.96236468 -60006.17965497
 -59584.98882938 -58283.15158291 -57790.54610343 -60773.74787331
 -60743.32073271 -58107.95700931 -58707.12476477 -59757.84870557
 -60279.54630941 -58667.025

[-57470.14831287 -57144.81781049 -57245.91099312 -57996.70751319
 -58267.72084464 -57147.6357624  -57558.2156764  -57846.10690041
 -57600.40389581 -57470.14831287 -58033.39369317 -57331.97937952
 -57790.54610343 -57490.97947831 -57144.81781049 -57490.97947831
 -58283.15158291 -57490.97947831 -56868.38682704 -57341.07746725
 -57452.99817759 -57341.07746725 -57594.96813435 -57790.54610343
 -58210.36334849 -57189.49569209 -57790.54610343 -57147.6357624
 -58152.36249948 -57610.18037062 -58144.64955762 -57490.97947831
 -57341.07746725 -57318.16331526 -57931.50042895 -57144.81781049
 -57910.21776095 -57158.16491525 -57931.50042895 -57558.2156764
 -57790.54610343 -57490.97947831 -57396.16079285 -57506.1220214
 -57490.97947831 -57594.96813435 -58795.0480092  -57396.16079285
 -58150.44258177 -57910.21776095 -58776.37932847 -58033.39369317
 -56868.38682704 -57331.97937952 -57790.54610343 -57662.31453936
 -57931.50042895 -57318.16331526 -57594.96813435 -57147.6357624
 -57452.99817759 -57846.10690

[-57162.66942858 -56799.99717022 -57245.91099312 -56970.76909055
 -57383.56081672 -57115.36895393 -57158.16491525 -57279.98801396
 -57134.2341958  -57365.83350288 -56899.32555594 -57088.31739867
 -56846.07002763   -664.79673284 -57144.81781049 -57260.19397803
 -57317.70336121 -57383.56081672 -56868.38682704 -56949.24081708
 -56943.32009666 -57341.07746725 -57267.03748493 -57105.00570848
 -57365.83350288 -57008.30360963 -57157.66882695 -57147.6357624
 -57610.18037062 -57189.49569209 -57302.92559211 -57444.75440369
 -56925.54791083 -56970.76909055 -57105.00570848 -57087.02497414
 -56970.76909055 -57158.16491525 -57391.59883939 -56949.24081708
 -56799.99717022 -56868.38682704 -57209.08090227 -57331.97937952
 -57195.27910232 -56733.14822288 -57312.57517457 -57203.38399333
 -56754.94339493   -664.79673284 -57510.14012979 -56943.32009666
 -56868.38682704   -664.79673284 -57058.91776947 -57053.31039801
 -57396.16079285 -57267.03748493 -57291.03567889 -56733.14822288
 -57088.31739867 -56868.38

[-56837.10141467 -56753.74353835   -849.45583668 -56970.76909055
 -57050.85085148 -56913.88042072 -56753.74353835 -56911.44145136
 -56972.1097669  -56837.10141467 -56868.38682704 -56855.38051635
 -56846.07002763   -664.79673284 -56664.23120009 -56925.54791083
 -56687.88381502 -57023.06168569 -56868.38682704 -56872.2243881
 -56830.71753458 -56990.77925109 -56772.87581216 -56943.32009666
 -57027.17990502 -56925.54791083 -56925.54791083 -56837.10141467
 -56753.74353835 -57027.17990502 -56925.54791083 -56970.76909055
 -56733.14822288 -56749.53974528 -56948.62882409 -56939.14981435
 -56949.24081708 -56817.06442292 -57037.21958364 -56733.14822288
 -56799.99717022 -56868.38682704 -56868.38682704 -56762.01065241
 -56830.71753458 -56733.14822288 -56993.78881215 -56871.52322313
 -56754.94339493   -664.79673284 -56733.14822288 -56943.32009666
 -56868.38682704   -664.79673284 -56846.07002763 -56749.53974528
 -56899.32555594 -57023.06168569 -56819.82962812 -56733.14822288
   -375.31414556 -56868.38

...

[-24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620

[-24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620

[-24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620

[-24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620

[-24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620907 -24.30620907 -24.30620907 -24.30620907 -24.30620907
 -24.30620

In [11]:
gbest[0]

array([2.17199664, 2.36368237, 8.77392577, 5.09598515, 0.99065423,
       1.430573  , 1.3216447 , 9.82872618, 8.28009197, 8.37592571])

In [12]:
G07(gbest[0])

(24.306209068262845,
 -2.5011104298755527e-12,
 -6.476597036453313e-12,
 -7.052136652418994e-12,
 -6.930065410415409e-10,
 -3.036859652638668e-11,
 -1.1936052146666043e-10,
 -6.148503282317492,
 -50.0239575578156)